In [1]:
import numpy as np
from numpy.linalg import inv
import scipy.linalg as sp
from scipy.linalg import eigh
import matplotlib.pyplot as plt
from math import ceil
import h5py
#import ana_cont.continuation as cont

In [2]:
def plot_object(x, f, label=None, axs=None):
    if label is not None:
        label_re = "Re(" + label + ")"
        label_im = "Im(" + label + ")"
    if axs is None:
        fig, axs = plt.subplots(1, 1, figsize=(8, 6))
    axs.plot(x, f.real, color="tab:blue", linewidth=2, label=label_re, linestyle="solid")
    axs.plot(x, f.imag, color="tab:orange", linewidth=2, label=label_im, linestyle="dashed")
    axs.legend()
    return axs

def S_iw_adjust(S_iw, hartree=0):
    Re = S_iw.real
    Im = S_iw.imag
    Re = Re - hartree
    print(r"Re(S) at w--> $\infty$: ", Re[-1])
    S_iw = Re + 1.j*Im
    return S_iw

def cut_matsubara(iw, function, nKeep, nStep):
    nRemove = (int)(len(iw) / 2)
    n_iw = iw[nRemove:]
    n_function_Re = function.real[nRemove:]
    n_function_Im = function.imag[nRemove:]
    n_iw = n_iw[:nKeep * nStep : nStep]
    n_function_Re = n_function_Re[:nKeep * nStep : nStep]
    n_function_Im = n_function_Im[:nKeep * nStep : nStep]
    return n_iw, n_function_Re + 1.j*n_function_Im

def plot_DMFT_convergence(DMFT_results, num_ineq):
    fig, axs = plt.subplots(4, num_ineq, figsize=(6*num_ineq,4*num_ineq), sharex=True)
    num_iter = DMFT_results._num_iter
    iters = np.arange(1, num_iter+1, 1)
    lw = 2
    if num_ineq == 1:
        label = "ineq-" + str(0)
        axs[0].set_title(label, fontsize=16)
        axs[0].set_ylabel("$\mu (eV)$")
        axs[0].plot(iters, DMFT_results.mu, label="$\mu$", linewidth=2, color="tab:blue")
    
        axs[1].set_ylabel("Occ.")
        occ = DMFT_results.occ
        axs[1].plot(iters, np.sum(occ, axis=1), label="Occ.", linewidth=2, color="tab:orange")
    
        axs[2].set_ylabel(r"$d\mathcal{G}_0$")
        axs[2].set_yscale("log")
        axs[2].plot(iters[0:num_iter-1]+1, DMFT_results.G0_iw_conv[0:num_iter-1], label=r"$d\mathcal{G}_0$", linewidth=2, color="tab:red")

        axs[3].set_ylabel(r"$|G_{imp}-G_{loc}$|")
        axs[3].set_yscale("log")
        axs[3].plot(iters[0:num_iter-1], DMFT_results.Gimp_Gloc_iw_conv[0:num_iter-1], label=r"$|G_{imp}-G_{loc}|$", linewidth=2, color="tab:purple")
        axs[3].set_xlabel(r"DMFT iteration")
    elif num_ineq > 1:
        for ineq in range(0, num_ineq):
            label = "ineq-" + str(ineq)
            axs[0][ineq].set_title(label, fontsize=16)
            axs[0][0].set_ylabel("$\mu (eV)$")
            axs[0][ineq].plot(iters, DMFT_results.mu, label="$\mu$", linewidth=2, color="tab:blue")
    
            axs[1][0].set_ylabel("Occ.")
            occ = np.array([array[ineq] for array in DMFT_results.occ])
            axs[1][ineq].plot(iters, np.sum(occ, axis=1), label="Occ.", linewidth=2, color="tab:orange")
    
            axs[2][0].set_ylabel(r"$d\mathcal{G}_0$")
            axs[2][ineq].set_yscale("log")
            axs[2][ineq].plot(iters[0:num_iter-1]+1, DMFT_results.G0_iw_conv[0:num_iter-1, ineq], label=r"$d\mathcal{G}_0$", linewidth=2, color="tab:red")

            axs[3][0].set_ylabel(r"$|G_{imp}-G_{loc}$|")
            axs[3][ineq].set_yscale("log")
            axs[3][ineq].plot(iters[0:num_iter-1], DMFT_results.Gimp_Gloc_iw_conv[0:num_iter-1, ineq], label=r"$|G_{imp}-G_{loc}|$", linewidth=2, color="tab:purple")
            axs[3][ineq].set_xlabel(r"DMFT iteration")

        plt.tight_layout()
        plt.show()
    return fig, axs


def return_band_occupations(DMFT_results, num_ineq):
    num_iter = DMFT_results._num_iter
    if num_ineq == 1:
        occ = DMFT_results.occ
        print("The single ineq. atom num. has the following occupation:")
        for num, orb in enumerate(occ[num_iter-1]):
            print(num+1, ":   ",  orb)
            print("Total:   ", np.sum(occ[num_iter-1]))
    elif num_ineq > 1:
        for ineq in range(0, num_ineq):
            occ = np.array([array[ineq] for array in DMFT_results.occ])
            print("Ineq. atom num. ", ineq ,"has the following occupations: ")
            for num, orb in enumerate(occ[num_iter-1]):
                print(num+1, ":   ",  orb)
            print("Total:   ", np.sum(occ[num_iter-1]))
    return 

In [3]:
def real_to_bloch(H, k):
    num_wann = H.num_wann
    Hk = np.zeros((num_wann,num_wann), dtype=complex)  ## Hamiltonian at point k
    ## For each k, the hamiltonian is converted from H_r
    for i, (idx, H_i) in enumerate(H.H_r.items()):     ## Iterate over real space vectors
        ## Fourier transform
        ## k and R are in crystal coordinates, so their scalar product has to be
        ## multiplied by 2*pi
        ## The factor H.ws_weights accounts for symmetries of the WS cell
        ## It's a division because this is a FT transform!
        ## H_i["idx"] contains the index of the Wannier function
        ## H_i["tb_idx"] contains the corresponding matrix element
   #     print(idx, H_i)
        Hk[H_i["idx"][0]-1][H_i["idx"][1]-1] += (H_i["tb_idx"] * np.exp( - 2*np.pi*1.j*np.dot(k, H.R[i]))/H.ws_weights_expanded[i] )
    return Hk

class Hamiltonian():
    def __init__(self, _n_dim):
        self._n_dim = 3     
        self.direct_lattice = np.zeros((self._n_dim,self._n_dim))    
        self.num_wann = 0
        self.num_ws_pts = 0
        self.ws_weights = 0
        self.H_r = {}
        self.R = {}
        self.ws_weights_expanded = {}
    def read_w90_hamiltonian_hr(self, path):
        with open(path, "r") as hr_file:
            lines = hr_file.readlines()
            self.num_wann = int(lines[1].strip())
            self.num_ws_pts = int(lines[2].strip())
            num_lines_weights = ceil(self.num_ws_pts/15)  ## Hardcoded in /wannier90/src/hamiltonian.F90
            lines_weights = [line.strip().split() for line in lines[3:3+num_lines_weights]] ## Weights of the WS cell in real space
            self.ws_weights = np.asarray([element for line in lines_weights for element in line], dtype=int)
            n_skip_lines = 3+num_lines_weights
            ## wannier90 file from now contain H_ij(r) 
            ## Where i, j are indices of the Wannier functions
            ## r is a position in space, r = l*a + m*b + n*c, with a, b, c lattice vectors
            ## It is written as follows:
            ## l m n  i   j  Re(H_ij(r))   Im(H_ij(r))
            line_idx = 0
            for rpts in range(0, self.num_ws_pts):
                for m_elm in range(0, self.num_wann**2):
                    line = lines[n_skip_lines+line_idx].strip().split()
                    self.R[line_idx] = np.asarray(line[0:3], dtype=int)
                    self.ws_weights_expanded[line_idx] = self.ws_weights[rpts]
                    H_site = np.asarray(line[0:3], dtype=int)
                    H_idx = np.asarray(line[3:5], dtype=int)
                    Re_H_idxr = np.asarray(line[5], dtype=float)
                    Im_H_idxr = np.asarray(line[6], dtype=float)
                    H_idxr = Re_H_idxr + 1.j * Im_H_idxr
                    self.H_r[line_idx] = {"idx" : H_idx, "site" : H_site, "tb_idx" : H_idxr}
                    line_idx += 1
    def curb_H_r(self, list_keep, rescale=1):
        for i, (idx, H_i) in enumerate(self.H_r.items()):
            if H_i["tb_idx"].real in list_keep:
                H_i["tb_idx"] = H_i["tb_idx"]/rescale
            else:
                H_i["tb_idx"] = 0+0.j
                

def export_entry_nospin_w2dyn(file_handle, Hk, k):
    file_handle.write(str(k[0]) + "   " +  str(k[1]) + "   " + str(k[2]) + "\n")
    size_i, size_j = Hk.shape
    for i in range(0, size_i):
        for j in range(0, size_j):
            file_handle.write(str(Hk[i][j].real) + "\t" + str(Hk[i][j].imag) + "\t")
        file_handle.write("\n")
    
def export_bloch_to_w2dyn(filename, H, n_kx, n_ky=None, n_kz=None):
    if n_ky is None:
        n_ky = n_kx
    if n_kz is None:
        n_kz = n_kx
        
    with open(filename, "w") as output_file:
#        output_file.write("## This file was converted from wannier90\n")
        output_file.write(str(n_kx*n_ky*n_kz) + "    " + str(H.num_wann) + "    " + str(H.num_wann) + "\n")
        ## Note that python's range does not include upper bound
        for kx in range(1, n_kx+1):
            for ky in range(1, n_ky+1):
                for kz in range(1, n_kz+1):
                    ## k-grid in reciprocal space in units of reciprocal lattice vector
                    ## kx, ky, kz go from 
                    k = np.asarray([(kx-1)/n_kx-1/2, (ky-1)/n_ky-1/2, (kz-1)/n_kz-1/2])
                    Hk = real_to_bloch(H, k)
                    export_entry_nospin_w2dyn(output_file, Hk, k)
                    
def gaussian(x, mean, std):
    return np.exp(-(x-mean)**2)/(2*std**2)/(np.sqrt(2*np.pi)*std)
def plot_DOS(H, wmin, wmax, npts, ngrdpts, gamma):
    dos = np.zeros(npts)
    wlist = np.array([wmin+(x-1)/(npts-1)*(wmax-wmin) for x in range(1, npts+1)])
    N = ngrdpts*ngrdpts*ngrdpts*np.pi
    for x in range(1, ngrdpts+1):
        for y in range(1, ngrdpts+1):
            for z in range(1, ngrdpts+1):
                k = np.array([(x-1)/ngrdpts, (y-1)/ngrdpts, (z-1)/ngrdpts])
                Hk = real_to_bloch(H, k)
                ek = sp.eigvals(Hk)
                for e in ek:
                    for i in range(npts):
                        dos[i] -= (np.sum(np.imag([1/(wlist[i]+1.j*gamma-x) for x in ek]))/N)
    plt.plot(wlist, dos)
    plt.show()
    return plt, wlist, dos
def get_Bandstructure(H, path, labels, n_pts, e1, e2, Efermi, 
                      silent=True, axs=None, rescale=1, plt_label=None):
    ## H --> Hamiltonian
    ## path in crystal coordinates, only special points
    ## labels for the special points (list)
    ## Num. of points from sp. point to sp. point
    ## e1, e2: energy minimum and maximum (for plotting, eV)
    n = H.num_wann
    if not silent:
        print("There are a total of ", n, " orbitals in the Hamiltonian")
    l = path.shape[0] 
    bands = np.zeros((n_pts*(l-1)+1, n)) 
    x = np.zeros(n_pts*(l-1)+1) ## Distance in k space
    lines = np.zeros(l)
    if axs is None:
        fig, axs = plt.subplots(1,1, figsize=(6,6))
    else: 
        fig = plt.gcf()
    bands[0,:] = np.real(eigh(real_to_bloch(H, path[0]))[0])
    for i in range(1, l): ## Loop over special k points
        k0 = path[i-1]    ## Initial point
        delta_k = path[i] - k0  ## Vector from sp. point to the next
        for j in range(0, n_pts): ## Loop over points between sp. points
            idx = (i-1)*n_pts + j
            bands[idx+1,:] = np.real(eigh(real_to_bloch(H, k0 + j*delta_k/n_pts))[0])
            x[idx+1] = x[idx] + np.sqrt(np.dot(delta_k,delta_k))/n_pts
        lines[i] = x[idx+1]
    for i in range(0, n):
        if i == 0 and plt_label is not None:
            axs.plot(x, (bands[:,i]-Efermi)*rescale, label=plt_label, color="black")
        else:
            axs.plot(x, (bands[:,i]-Efermi)*rescale, label=None, color="black")
    axs.set_xticks(lines, labels)
    axs.xaxis.grid(color="black", linewidth=1)
    axs.set_xlim([0, x[-1]])
    axs.set_ylim([e1, e2])
#    plt.show()
    return fig, axs, bands, x
            
    

In [4]:
class w2dyn():
    def __init__(self, _num_iter = 0, beta = 39, _num_ineq = 1):
        self.beta = 0
        self._num_iter = _num_iter
        self._num_ineq = _num_ineq
        
        ## Observables that should converge over the DMFT loops
        self.mu = np.zeros(_num_iter)
        self.lda_mu = 0
        self.A_w0 = np.zeros((_num_iter, self._num_ineq))
        self.G0_iw_conv = np.zeros((_num_iter, self._num_ineq))
        self.Gimp_Gloc_iw_conv = np.zeros((_num_iter, self._num_ineq))
        self.iw = 0
        self.tau = 0
        self.w_dos = 0
        ## Declared as dictionaries, one entry per inequivalent atom
        ## Orbital resolved
        self.occ = []
        self.dc = {}
        ## Noninteracting G0, Matsubara
        self.G0_iw_m_s = {}
        self.G0_iw = {}
        ## Full G, Matsubara
        self.G_iw_m_s = {}
        self.G_iw = {}
        ## Full G, im. time
        self.G_tau_m_s = {}
        self.G_tau = {}
        ## Full selfenergy, Matsubara
        self.S_iw_m_s = {}
        self.S_iw = {}
        ## Error on selfenergy, Matsubara
        self.S_iw_m_s_err = {} 
        self.S_iw_err = {} 
        ## Moments of the self energy
        self.smom_m_s = {}
        self.smom_m = {}
        self.smom = {}        
        ## number of Matsubara freqs
        self.niw_full = {}
        self.lda_dos_m_s = 0
    
    def sum_bands_spins_G(self, f_m_s):
        f_s = np.sum(f_m_s, axis=0) 
        f = np.sum(f_s, axis=0) 
        return f
    
    def sum_bands_spins_S(self, f_m_s):
        f = np.diagonal(np.diagonal(f_m_s, axis1=0, axis2=2), axis1=0, axis2=1).transpose((1,2,0))
        f = np.mean(f, axis=(0,1))
        return f
#    def get_lda_mu(self, path):  # return: sigma, jk_error
#        with h5py.File(path "r") as F:
#            mu = F["start/lda-mu/value"][:]
#        return mu

    def get_results(self, path):
        with h5py.File(path, "r") as data:
            ## axes    
            self.iw = data[".axes"]["iw"][()]
            self.tau = data[".axes"]["tau"][()]
            self.w_dos = data[".axes"]["w-dos"][()]
#            self.beta = data['.config'].attrs['general.beta']['value'][()]
            ## Misc
#            self.dft_mu = data[]
            for ineq in range(0, self._num_ineq):
                if ineq < 10:
                    ineq_label = "ineq-00{}".format(ineq+1)
                else:
                    raise Exception("Too many inequivalent atoms!")
                self.dc[ineq] = data["dmft-last"][ineq_label]["dc"]["value"][()]
                ## G_iw resolved bands, spins and atoms
                self.G0_iw_m_s[ineq] = data["dmft-last"][ineq_label]["g0iw"]["value"][()]
                self.G0_iw[ineq] = self.sum_bands_spins_G(self.G0_iw_m_s[ineq])
                self.G_iw_m_s[ineq] = data["dmft-last"][ineq_label]["giw"]["value"][()]
                self.G_iw[ineq] = self.sum_bands_spins_G(self.G_iw_m_s[ineq])
                self.G_tau_m_s[ineq] = data["dmft-last"][ineq_label]["gtau-full"]["value"][()]
                self.G_tau[ineq] = self.sum_bands_spins_G(self.G_tau_m_s[ineq])
                ## S_iw resolved in bands and spins
                self.S_iw_m_s[ineq] = data["dmft-last"][ineq_label]["siw-full"]["value"][()]
                self.S_iw[ineq] = self.sum_bands_spins_S(self.S_iw_m_s[ineq])
                ## S_iw error
                self.S_iw_m_s_err[ineq] = data["dmft-last"][ineq_label]["siw-full"]["error"][:]
                self.S_iw_err[ineq] = self.sum_bands_spins_S(self.S_iw_m_s_err[ineq])
                self.S_iw_err[ineq] = self.S_iw_err[ineq]/np.sqrt(6)
                self.niw_full[ineq] = self.S_iw[ineq].shape[-1] // 2
                ## Selfenergy moments
                self.smom_m_s[ineq] = data["dmft-last"][ineq_label]["smom"]["value"][()]
                self.smom_m[ineq] = np.mean(self.smom_m_s[ineq], axis=1)
                self.smom[ineq] = np.mean(self.smom_m_s[ineq], axis=(0,1))
            
            ## Import from all DMFT iterations to check convergence
            if self._num_iter < 10:
                dmft_nm1 = "dmft-00" + str(self._num_iter)
            elif self._num_iter < 100:
                dmft_nm1 = "dmft-0" + str(self._num_iter)
            else:
                raise Exception("Sorry, too many iterations in your DMFT calculation")
            ## DFT dos resolved in bands and spins
            self.lda_dos_m_s = data["start"]["lda-dos"]["value"][()]
            self.lda_dos = self.sum_bands_spins_G(self.lda_dos_m_s)

            iter_previous = "dmft-000"
            for i in range(1, self._num_iter+1):
                if i < 10:
                    iter_name = "dmft-00" + str(i)
                elif i < 100:
                    iter_name = "dmft-0" + str(i)
                elif i < 1000:
                    iter_name = "dmft-" + str(i)
                else:
                    raise Exception("Too many dmft iterations")
                ## Observables that should converge over the loops    
                self.mu[i-1] = data[iter_name]["mu"]["value"][()]
                index_tau2 = np.argmin(np.abs(self.tau-self.beta/2))
                ## Iteration over inequivalent atoms
                occ_iter = []
                for ineq in range(0, self._num_ineq):
                    if ineq < 10:
                        ineq_label = "ineq-00{}".format(ineq+1)
                    occ_iter.append(np.diagonal(np.sum(np.diagonal(data["dmft-last"][ineq_label]["occ"]["value"][()], axis1=1, axis2=3), axis=2)))
                    self.A_w0[i-1][ineq] = -self.beta/np.pi * np.sum(self.G_tau_m_s[ineq][:,:,index_tau2])
                    self.Gimp_Gloc_iw_conv[i-1][ineq] = np.abs(np.trapz(self.sum_bands_spins_G(data[iter_name][ineq_label]["g0iw"]["value"][:])
                               -self.sum_bands_spins_G(data[iter_name][ineq_label]["giw"]["value"][:]), self.iw)).real
                    if i > 1:
                        self.G0_iw_conv[i-2][ineq] = np.abs(np.trapz(self.sum_bands_spins_G(data[iter_name][ineq_label]["g0iw"]["value"][:])
                                -self.sum_bands_spins_G(data[iter_previous][ineq_label]["g0iw"]["value"][:]), self.iw)).real
                    iter_previous = iter_name
                self.occ.append(occ_iter)

In [5]:
def get_Hk(H, path, labels, n_pts):
    n = H.num_wann
    l = path.shape[0] 
    Hk = np.zeros((n_pts*(l-1)+1, n, n)) + 0.j
    x = np.zeros(n_pts*(l-1)+1) ## Distance in k space
    lines = np.zeros(l)
    Hk[0,:,:] = real_to_bloch(H, path[0])
    for i in range(1, l): ## Loop over special k points
        k0 = path[i-1]    ## Initial point
        delta_k = path[i] - k0  ## Vector from sp. point to the next
        for j in range(0, n_pts): ## Loop over points between sp. points
            ik = (i-1)*n_pts + j
            x[ik+1] = x[ik] + np.sqrt(np.dot(delta_k,delta_k))/n_pts
            Hk[ik+1,:,:] = real_to_bloch(H, k0 + (j+1)*delta_k/n_pts)
        lines[i] = x[ik+1]
    return x, Hk, lines